In [1]:
import numpy as np
import pandas as pd
import os
import torch
from torch.autograd import Variable
import sys
!pip3 install skipthoughts
from skipthoughts import BiSkip

In [2]:
!pwd

/kaggle/working


In [3]:
!mkdir data

In [4]:
!cp -r ../input/dictionary/ data/dictionary

In [5]:
!cp -r ../input/fake-news-classification/ data/dataset

In [6]:
os.chdir('data/')

In [7]:
train_bdy = pd.read_csv('dataset/train_bodies.csv')
train_stnc = pd.read_csv('dataset/train_stances.csv')
test_bdy = pd.read_csv('dataset/competition_test_bodies.csv')
test_stnc = pd.read_csv('dataset/competition_test_stances.csv')

In [8]:
train_bdy.head()

Body ID                                        articleBody
0        0  A small meteorite crashed into a wooded area i...
1        4  Last week we hinted at what was to come as Ebo...
2        5  (NEWSER) – Wonder how long a Quarter Pounder w...
3        6  Posting photos of a gun-toting child online, I...
4        7  At least 25 suspected Boko Haram insurgents we...

In [9]:
test_bdy.head()

Body ID                                        articleBody
0        1  Al-Sisi has denied Israeli reports stating tha...
1        2  A bereaved Afghan mother took revenge on the T...
2        3  CNBC is reporting Tesla has chosen Nevada as t...
3       12  A 4-inch version of the iPhone 6 is said to be...
4       19  GR editor’s Note\n\nThere are no reports in th...

In [10]:
test_stnc.head()

Headline  Body ID     Stance
0  Ferguson riots: Pregnant woman loses eye after...     2008  unrelated
1  Crazy Conservatives Are Sure a Gitmo Detainee ...     1550  unrelated
2  A Russian Guy Says His Justin Bieber Ringtone ...        2  unrelated
3  Zombie Cat: Buried Kitty Believed Dead, Meows ...     1793  unrelated
4  Argentina's President Adopts Boy to End Werewo...       37  unrelated

In [11]:
train_stnc.head()

Headline  Body ID     Stance
0  Police find mass graves with at least '15 bodi...      712  unrelated
1  Hundreds of Palestinians flee floods in Gaza a...      158      agree
2  Christian Bale passes on role of Steve Jobs, a...      137  unrelated
3  HBO and Apple in Talks for $15/Month Apple TV ...     1034  unrelated
4  Spider burrowed through tourist's stomach and ...     1923   disagree

In [12]:
def preprocess(s):
    s = s.lower()
    s = s.replace("\n","")
    s = s.replace("\'s"," is")
    s = s.replace("n\'t"," not")
    s = s.replace("\'d"," would")
    return s

In [13]:
def id2body(_id,df):
    return df[df['Body ID'] == _id]['articleBody'].values[0]

In [14]:
id2body(7, train_bdy)

'At least 25 suspected Boko Haram insurgents were killed in clashes between soldiers and the Islamist militants in northeast Nigeria and five civilians were killed in fighting elsewhere in the region, a military source and residents said on Monday.\n\nA ceasefire agreement between Boko Haram and the Nigerian government was expected to lead to the liberation of more than 200 schoolgirls kidnapped by the militants six months ago, and talks were due to continue in neighbouring Chad on Monday.\n\nBoko Haram has not confirmed the truce and there have been at least six attacks over the weekend – blamed by security sources on the insurgents – that have killed several dozen people since the announcement of the ceasefire.\n\nA government spokesman has said that the fighting on Sunday may be the work of criminal gangs in the lawless region.\n\nAn army officer, who requested anonymity, said the militants tried to enter the town of Damboa late on Sunday through Alagarno, a Boko Haram hideout, but 

In [15]:
preprocess("Hi, I am lokesh. That's my phone. Don't touch it")

'hi, i am lokesh. that is my phone. do not touch it'

In [16]:
def generate_csv(bdy_df,stnc_df,file):
    heads = []
    bodies = []
    stances = []
    head_wc = []
    bdy_wc = []
    for i in range(len(stnc_df)):
        head = preprocess(stnc_df['Headline'][i])
        _id = stnc_df['Body ID'][i]
        body = preprocess(id2body(_id, bdy_df))
        stance = preprocess(stnc_df['Stance'][i])
        heads.append(head)
        stances.append(stance)
        bodies.append(body)
        head_wc.append(len(head.split()))
        bdy_wc.append(len(body.split()))
    df = pd.DataFrame()
    df['Headline'] = heads
    df['Body'] = bodies
    df['Stance'] = stances
    df['Headline Word Count'] = head_wc
    df['Body Word Count'] = bdy_wc
    df.to_csv("dataset/"+file)


In [17]:
generate_csv(train_bdy, train_stnc, "train.csv")
generate_csv(test_bdy, test_stnc, "test.csv")

In [18]:
def generate_dict():
    f = open("dictionary/dictionary.txt", "r")
    data = f.read()
    data_lst = data.replace('\n', ' ').split(" ")
    vocab = list(set(data_lst))

    w2i = {}
    for i in range(len(vocab)):
        w2i[vocab[i]] = i+1
    return vocab, w2i

In [19]:
vocab, w2i = generate_dict()

In [20]:
dir_st = 'skipthoughts'
biskip = BiSkip(dir_st, vocab)

--2023-11-20 17:39:38--  http://www.cs.toronto.edu/~rkiros/models/dictionary.txt
Resolving www.cs.toronto.edu (www.cs.toronto.edu)... 128.100.3.30
Connecting to www.cs.toronto.edu (www.cs.toronto.edu)|128.100.3.30|:80... 

connected.
HTTP request sent, awaiting response... 200 OK
Length: 7996547 (7.6M) [text/plain]
Saving to: ‘skipthoughts/dictionary.txt’

     0K .......... ...

....... .......... .......... ..........  0%  130K 60s
    50K .......... .......... .......... .......... ........

..  1%  261K 44s
   100K .......... .......... .......... .......... ..........  1% 22.3M 29s
   150K .......... .......... .......... .......... ..........  2% 22.4M 22s
   200K .......... .......... .......... .......... ..........  3%  265K 23s
   250K .......... .......... .......... .......... ..........  3% 21.4M 19s
   300K .......... .......... .......... .......... ..........  4% 20.9M 16s
   350K .......... .......... .......... .......... ..........  5% 24.0M 14s
   400K .......... .......... ...

....... .......... ..........  5%  272K 16s
   450K .......... .......... .......... .......... ..........  6% 20.6M 14s
   500K .......... .......... .......... .......... ..........  7% 19.4M 13s
   550K .......... .......... .......... .......... ..........  7% 20.0M 12s
   600K .......... .......... .......... .......... ..........  8% 19.9M 11s
   650K .......... .......... .......... .......... ..........  8% 21.9M 10s
   700K .......... .......... .......... .......... ..........  9% 22.2M 9s
   750K .......... .......... .......... .......... .......... 10% 23.4M 9s
   800K .......... .......... .......... .......... ...

...

..... .......... .......... 95% 4.13M 1s
268550K .......... .......... .......... .......... .......... 95% 41.6M 1s
268600K .......... .......... .......... .......... .......... 95%  133M 1s
268650K .......... .......... .......... .......... .......... 95% 1.54M 1s
268700K .......... .......... .......... .......... .......... 95% 43.5M 1s
268750K .......... .......... .......... .......... .......... 95% 22.5M 1s
268800K .......... .......... .......... .......... .......... 95% 97.6M 1s
268850K .......... .......... .......... .......... .......... 95%  102M 1s
268900K .......... .......... .......... .......... .......... 95% 6.48M 1s
268950K .......... .......... .......... .......... .......... 95%  111M 1s
269000K .......... .......... .......... .......... .......... 95% 7.53M 1s
269050K .......... .......... .......... .......... .......... 95%  115M 1s
269100K .......... .......... .......... .......... .......... 95%  123M 1s
269150K .......... .......... .......... ......

....... .......... .......... .......... .......... 96% 39.3M 1s
272200K .......... .......... .......... .......... .......... 96% 42.5M 1s
272250K .......... .......... .......... .......... .......... 96% 44.5M 1s
272300K .......... .......... .......... .......... .......... 96% 42.3M 1s
272350K .......... .......... .......... .......... .......... 96%  158M 1s
272400K .......... .......... .......... .......... .......... 96% 39.7M 1s
272450K .......... .......... .......... .......... .......... 96%  909K 1s
272500K .......... .......... .......... .......... .......... 96%  115M 1s
272550K .......... .......... .......... .......... .......... 96% 23.4M 1s
272600K .......... .......... .......... .......... .......... 96% 82.9M 1s
272650K .......... .......... .......... .......... .......... 96%  149M 1s
272700K .......... .......... .......... .......... .......... 96% 61.2M 1s
272750K .......... .......... .......... .......... .......... 96% 5.70M 1s
272800K .......... ....

.. 97% 6.63M 1s
274700K .......... .......... .......... .......... .......... 97%  122M 0s
274750K .......... .......... .......... .......... .......... 97%  109M 0s
274800K .......... .......... .......... .......... .......... 97% 69.7M 0s
274850K .......... .......... .......... .......... .......... 97% 76.3M 0s
274900K .......... .......... .......... .......... .......... 97%  112M 0s
274950K .......... .......... .......... .......... .......... 97% 87.3M 0s
275000K .......... .......... .......... .......... .......... 97% 84.4M 0s
275050K .......... .......... .......... .......... .......... 97% 69.2M 0s
275100K .......... .......... .......... .......... .......... 97%  128M 0s
275150K .......... .......... .......... .......... .......... 97%  109M 0s
275200K .......... .......... .......... .......... .......... 97% 88.0M 0s
275250K .......... .......... .......... .......... .......... 97% 94.8M 0s
275300K .......... .......... .......... .......... .......... 97% 39.1M

........ .......... .......... .......... .......... 98% 2.73M 0s
278500K .......... .......... .......... .......... .......... 98% 83.1M 0s
278550K .......... .......... .......... .......... .......... 98% 33.2M 0s
278600K .......... .......... .......... .......... .......... 98%  134M 0s
278650K .......... .......... .......... .......... .......... 98% 98.2M 0s
278700K .......... .......... .......... .......... .......... 98%  124M 0s
278750K .......... .......... .......... .......... .......... 98% 5.10M 0s
278800K .......... .......... .......... .......... .......... 98%  114M 0s
278850K .......... .......... .......... .......... .......... 98% 4.75M 0s
278900K .......... .......... .......... .......... .......... 98% 97.9M 0s
278950K .......... .......... .......... .......... .......... 98% 96.5M 0s
279000K .......... .......... .......... .......... .......... 98% 34.2M 0s
279050K .......... .......... .......... .......... .......... 98% 37.7M 0s
279100K .......... ...

...... .......... 99% 1.29M 0s
282350K .......... .......... .......... .......... .......... 99%  132M 0s
282400K .......... .......... .......... .......... .......... 99%  106M 0s
282450K .......... .......... .......... .......... .......... 99% 28.1M 0s
282500K .......... .......... .......... .......... .......... 99%  112M 0s
282550K ........                                              100%  193M=18s

2023-11-20 17:42:53 (15.4 MB/s) - ‘skipthoughts/bi_skip.npz’ saved [289340074/289340074]



In [21]:
import pickle

In [22]:
!mkdir model

In [23]:
pickle.dump(w2i, open('model/w2i.pkl', 'wb'))
pickle.dump(biskip, open('model/biskip.pkl', 'wb'))

In [24]:
w2i = pickle.load(open('model/w2i.pkl', 'rb'))
biskip = pickle.load(open('model/biskip.pkl', 'rb'))

In [25]:
%load_ext memory_profiler

In [26]:
def neural_features(path):
    df = pd.read_csv(path)
    heads, bodies = df['Headline'], df['Body']

    MAX_HEADLINE_COUNT = df['Headline Word Count'].max()
    MAX_BODY_COUNT = df['Body Word Count'].max()
    
    head_ids = np.zeros((len(heads), MAX_HEADLINE_COUNT + 1), dtype=np.float32)
    bdy_ids = np.zeros((len(bodies), MAX_BODY_COUNT + 1), dtype=np.float32)
    
    head_encodings = np.zeros((len(heads), 2400), dtype=np.float32)
    bdy_encodings = np.zeros((len(bodies), 2400), dtype=np.float32)
    BATCH_SZ = 200
    %memit
    
    for i in range(len(heads)):
        hl = heads[i].split()
        body = bodies[i].split()

        for j, word in enumerate(hl):
            try:
                head_ids[i][j] = w2i[word]
            except KeyError:
                pass
        for j, word in enumerate(body):
            try:
                bdy_ids[i][j] = w2i[word]
            except KeyError:
                pass
        if sum(head_ids[i])==0:
            head_ids[i][-1] = len(w2i)
        if sum(bdy_ids[i])==0:
            bdy_ids[i][-1] = len(w2i)
    print("chk-pt 1")
    print()
    
    rem = len(heads) % BATCH_SZ
    print("##############################################")
    
    for i in range(0, len(heads), BATCH_SZ):
        print(i)
        h = torch.LongTensor(head_ids[i:i+BATCH_SZ])
        b = torch.LongTensor(bdy_ids[i:i+BATCH_SZ])

        h_tmp = biskip(h).detach().numpy()
        b_tmp = biskip(b).detach().numpy()
        
        head_encodings[i:i+BATCH_SZ] = h_tmp[:BATCH_SZ]
        bdy_encodings[i:i+BATCH_SZ] = b_tmp[:BATCH_SZ]
        
        
    if rem != 0:
        print(rem)
        h = torch.LongTensor(head_ids[len(heads)-rem:])
        b = torch.LongTensor(bdy_ids[len(heads)-rem:])
            
        h_tmp = biskip(h).detach().numpy()
        b_tmp = biskip(b).detach().numpy()
        
        head_encodings[len(heads)-rem:] = h_tmp
        bdy_encodings[len(heads)-rem:] = b_tmp
    print("##############################################")
    print()
    print("chk-pt 2")
    
    feat1 = np.zeros((len(heads), 2400), dtype=np.float32)
    feat2 = np.zeros((len(heads), 2400), dtype=np.float32)
    
    for j, (h_vector, b_vector) in enumerate(zip(head_encodings, bdy_encodings)):
        feat1[j] = np.multiply(h_vector, b_vector)
        feat2[j] = np.absolute(h_vector - b_vector)

    print("chk-pt 3")
    
    features = np.concatenate((feat1, feat2), axis=1)
    return features


In [27]:
neural_features_train = neural_features('dataset/train.csv')

peak memory: 4011.57 MiB, increment: 0.00 MiB


chk-pt 1

##############################################
0


200


400


600


800


1000


1200


In [ ]:
neural_features_train.shape

In [ ]:
!mkdir features

In [ ]:
np.save(arr=neural_features_train,file='features/train_nf.npy')

In [ ]:
neural_features_test = neural_features('dataset/test.csv')

In [ ]:
neural_features_test.shape

In [ ]:
np.save(arr=neural_features_test,file='features/test_nf.npy')

In [ ]:
neural_features_test.shape

In [ ]:
neural_features_train.shape